In [12]:
import json
import numpy as np
import pandas as pd

In [18]:
df = pd.read_csv(
    "../data/BC2GM-IOB/train.tsv", 
    sep="\s", header=None, 
    names=["text", "label"]
)
df

/Users/xu081/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:4: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  after removing the cwd from sys.path.


text   label
0       Immunohistochemical       O
1                  staining       O
2                       was       O
3                  positive       O
4                       for       O
...                     ...     ...
355400                depot       O
355401                    )       O
355402                  and       O
355403       gonadotrophins  B-GENE
355404                    .       O

[355405 rows x 2 columns]

In [103]:
label_check = {label: i for i, label in enumerate(df.label)}
label_check

{'O': 355404, 'B-GENE': 355403, 'I-GENE': 355396}

In [90]:
def format_ner_data(data_path):
    """
    Reformat NER data as 
    text = [
        [w_1, w_2, ..., w_k1],
        [w_1, w_2, ..., w_k2],
        ...
        [w_1, w_2, ..., w_kn],
    ]
    labels = [
        [ent_1, ent_2, ..., ent_k1],
        [ent_1, ent_2, ..., ent_k2],
        ...
        [ent_1, ent_2, ..., ent_kn]
    ]
    """

    with open(data_path, "r") as f:
        x = csv.reader(f, delimiter='\t', quoting=csv.QUOTE_NONE)
        text_arr = []
        label_arr = []
        
        curr_sent = []
        curr_label = []
        for row in x:
            if len(row) > 0:
#                 print(row[0])
                curr_sent.append(row[0]) 
#                 print(row[1])
                curr_label.append(row[1])
            else:
                text_arr.append(curr_sent)
                label_arr.append(curr_label)
                curr_sent = []
                curr_label = []
    return text_arr, label_arr

In [91]:
text_arr, label_arr = format_ner_data("../data/BC2GM-IOB/train.tsv")

In [93]:
text_arr[12573]

['The',
 'patient',
 'underwent',
 'two',
 'intracytoplasmic',
 'sperm',
 'injection',
 'cycles',
 'with',
 'thawed',
 'epididymal',
 'spermatozoa',
 ',',
 'in',
 'which',
 ',',
 'due',
 'to',
 'a',
 'pharmacist',
 "'",
 's',
 'mistake',
 ',',
 'ovarian',
 'stimulation',
 'was',
 'carried',
 'out',
 'by',
 'a',
 'combination',
 'of',
 'long',
 '-',
 'acting',
 'gonadotrophin',
 '-',
 'releasing',
 'hormone',
 'agonist',
 '(',
 'leuprolide',
 'depot',
 ')',
 'and',
 'gonadotrophins',
 '.']

In [95]:
len(text_arr)

12574

In [96]:
len(label_arr)

12574

In [101]:
test_label = [
    ["a", "a", "c"],
    ["b", "c", "d"]
]

{label: i for label_sent in test_label for i, label in enumerate(label_sent)}

{'a': 1, 'c': 1, 'b': 0, 'd': 2}

In [105]:
arr_sl = []
i = 0
for s, l in zip(text_arr, label_arr):
    print(s)
    print(l)
    arr_sl.append((s, l))
    if i > 5:
        break
    i += 1
arr_sl

['Immunohistochemical', 'staining', 'was', 'positive', 'for', 'S', '-', '100', 'in', 'all', '9', 'cases', 'stained', ',', 'positive', 'for', 'HMB', '-', '45', 'in', '9', '(', '90', '%', ')', 'of', '10', ',', 'and', 'negative', 'for', 'cytokeratin', 'in', 'all', '9', 'cases', 'in', 'which', 'myxoid', 'melanoma', 'remained', 'in', 'the', 'block', 'after', 'previous', 'sections', '.']
['O', 'O', 'O', 'O', 'O', 'B-GENE', 'I-GENE', 'I-GENE', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-GENE', 'I-GENE', 'I-GENE', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B-GENE', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O']
['Chloramphenicol', 'acetyltransferase', 'assays', 'examining', 'the', 'ability', 'of', 'IE86', 'to', 'repress', 'activity', 'from', 'the', 'HCMV', 'major', 'IE', 'promoter', 'or', 'activate', 'the', 'HCMV', 'early', 'promoter', 'for', 'the', '2', '.', '2', '-', 'kb', 'class', 'of', 'RNAs', 'demonstrated', 'the', 'functional', 'integrity

[(['Immunohistochemical',
   'staining',
   'was',
   'positive',
   'for',
   'S',
   '-',
   '100',
   'in',
   'all',
   '9',
   'cases',
   'stained',
   ',',
   'positive',
   'for',
   'HMB',
   '-',
   '45',
   'in',
   '9',
   '(',
   '90',
   '%',
   ')',
   'of',
   '10',
   ',',
   'and',
   'negative',
   'for',
   'cytokeratin',
   'in',
   'all',
   '9',
   'cases',
   'in',
   'which',
   'myxoid',
   'melanoma',
   'remained',
   'in',
   'the',
   'block',
   'after',
   'previous',
   'sections',
   '.'],
  ['O',
   'O',
   'O',
   'O',
   'O',
   'B-GENE',
   'I-GENE',
   'I-GENE',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'B-GENE',
   'I-GENE',
   'I-GENE',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'B-GENE',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O',
   'O']),
 (['Chloramphenicol',
   'acetyltransferase',
   '

In [108]:
seq_a, lab_a = list(zip(*arr_sl))

In [110]:
list(seq_a)

[['Immunohistochemical',
  'staining',
  'was',
  'positive',
  'for',
  'S',
  '-',
  '100',
  'in',
  'all',
  '9',
  'cases',
  'stained',
  ',',
  'positive',
  'for',
  'HMB',
  '-',
  '45',
  'in',
  '9',
  '(',
  '90',
  '%',
  ')',
  'of',
  '10',
  ',',
  'and',
  'negative',
  'for',
  'cytokeratin',
  'in',
  'all',
  '9',
  'cases',
  'in',
  'which',
  'myxoid',
  'melanoma',
  'remained',
  'in',
  'the',
  'block',
  'after',
  'previous',
  'sections',
  '.'],
 ['Chloramphenicol',
  'acetyltransferase',
  'assays',
  'examining',
  'the',
  'ability',
  'of',
  'IE86',
  'to',
  'repress',
  'activity',
  'from',
  'the',
  'HCMV',
  'major',
  'IE',
  'promoter',
  'or',
  'activate',
  'the',
  'HCMV',
  'early',
  'promoter',
  'for',
  'the',
  '2',
  '.',
  '2',
  '-',
  'kb',
  'class',
  'of',
  'RNAs',
  'demonstrated',
  'the',
  'functional',
  'integrity',
  'of',
  'the',
  'IE86',
  'protein',
  '.'],
 ['A',
  'new',
  'DNA',
  'repair',
  'gene',
  'from',

In [127]:
# import csv

# with open("../data/BC2GM-IOB/train_sample.tsv", "r") as f:
#     x = csv.reader(f, delimiter='\t')
# #     for row in x:
# #         if len(row) > 0:
# #             print(row[0])
# #             print(row[1])
# #         else:
# #             print("------\n------\n------\n")
# #             print("blank_space")
# #             print("------\n------\n------\n")
#     print(xx)
#     label_map = {label: i for i, label in enumerate(x)}
#     print(label_map)

TypeError: unhashable type: 'list'

In [24]:
i = 0
for r in df.iterrows():
    print(r)
    if i > 100:
        break
    i += 1

(0, text     Immunohistochemical
label                      O
Name: 0, dtype: object)
(1, text     staining
label           O
Name: 1, dtype: object)
(2, text     was
label      O
Name: 2, dtype: object)
(3, text     positive
label           O
Name: 3, dtype: object)
(4, text     for
label      O
Name: 4, dtype: object)
(5, text          S
label    B-GENE
Name: 5, dtype: object)
(6, text          -
label    I-GENE
Name: 6, dtype: object)
(7, text        100
label    I-GENE
Name: 7, dtype: object)
(8, text     in
label     O
Name: 8, dtype: object)
(9, text     all
label      O
Name: 9, dtype: object)
(10, text     9
label    O
Name: 10, dtype: object)
(11, text     cases
label        O
Name: 11, dtype: object)
(12, text     stained
label          O
Name: 12, dtype: object)
(13, text     ,
label    O
Name: 13, dtype: object)
(14, text     positive
label           O
Name: 14, dtype: object)
(15, text     for
label      O
Name: 15, dtype: object)
(16, text        HMB
label    B-GENE
Name:

In [17]:
df.label.unique()

array(['O', 'B-GENE', 'I-GENE'], dtype=object)

In [19]:
label_map = {label: i for i, label in enumerate(df.label)}

In [20]:
label_map

{'O': 355404, 'B-GENE': 355403, 'I-GENE': 355396}

In [22]:
for i, label in enumerate(df.label):
    print(i, label)

0 O
1 O
2 O
3 O
4 O
5 B-GENE
6 I-GENE
7 I-GENE
8 O
9 O
10 O
11 O
12 O
13 O
14 O
15 O
16 B-GENE
17 I-GENE
18 I-GENE
19 O
20 O
21 O
22 O
23 O
24 O
25 O
26 O
27 O
28 O
29 O
30 O
31 B-GENE
32 O
33 O
34 O
35 O
36 O
37 O
38 O
39 O
40 O
41 O
42 O
43 O
44 O
45 O
46 O
47 O
48 B-GENE
49 I-GENE
50 O
51 O
52 O
53 O
54 O
55 B-GENE
56 O
57 O
58 O
59 O
60 O
61 O
62 O
63 B-GENE
64 I-GENE
65 O
66 O
67 O
68 B-GENE
69 I-GENE
70 I-GENE
71 O
72 O
73 O
74 O
75 O
76 O
77 O
78 O
79 O
80 O
81 O
82 O
83 O
84 O
85 O
86 O
87 B-GENE
88 I-GENE
89 O
90 O
91 O
92 B-GENE
93 I-GENE
94 I-GENE
95 O
96 O
97 O
98 O
99 O
100 O
101 B-GENE
102 O
103 O
104 O
105 O
106 O
107 O
108 O
109 O
110 O
111 O
112 O
113 O
114 O
115 O
116 O
117 O
118 O
119 O
120 O
121 O
122 O
123 O
124 O
125 O
126 O
127 O
128 O
129 O
130 O
131 O
132 O
133 O
134 O
135 O
136 O
137 O
138 O
139 O
140 O
141 O
142 O
143 O
144 O
145 O
146 O
147 O
148 B-GENE
149 O
150 O
151 O
152 O
153 O
154 O
155 O
156 O
157 O
158 O
159 O
160 O
161 O
162 O
163 O
164 O
165 O
166 

1577 O
1578 O
1579 O
1580 O
1581 O
1582 O
1583 O
1584 O
1585 O
1586 O
1587 O
1588 O
1589 O
1590 O
1591 O
1592 O
1593 O
1594 O
1595 O
1596 O
1597 O
1598 O
1599 O
1600 O
1601 O
1602 O
1603 O
1604 O
1605 O
1606 O
1607 O
1608 O
1609 O
1610 O
1611 O
1612 O
1613 O
1614 O
1615 O
1616 O
1617 O
1618 O
1619 O
1620 O
1621 O
1622 O
1623 O
1624 O
1625 O
1626 O
1627 O
1628 O
1629 O
1630 O
1631 O
1632 O
1633 O
1634 O
1635 O
1636 O
1637 O
1638 O
1639 O
1640 O
1641 O
1642 B-GENE
1643 I-GENE
1644 O
1645 B-GENE
1646 O
1647 O
1648 O
1649 O
1650 O
1651 O
1652 O
1653 O
1654 O
1655 O
1656 O
1657 O
1658 O
1659 O
1660 O
1661 O
1662 O
1663 O
1664 O
1665 O
1666 O
1667 O
1668 O
1669 O
1670 O
1671 O
1672 O
1673 O
1674 O
1675 O
1676 O
1677 O
1678 O
1679 O
1680 O
1681 O
1682 O
1683 O
1684 O
1685 O
1686 O
1687 O
1688 O
1689 O
1690 O
1691 O
1692 O
1693 O
1694 O
1695 O
1696 O
1697 O
1698 O
1699 O
1700 O
1701 O
1702 O
1703 O
1704 O
1705 O
1706 O
1707 O
1708 O
1709 O
1710 O
1711 O
1712 O
1713 O
1714 O
1715 O
1716 O
1717 

2836 I-GENE
2837 I-GENE
2838 I-GENE
2839 I-GENE
2840 O
2841 O
2842 B-GENE
2843 I-GENE
2844 I-GENE
2845 I-GENE
2846 O
2847 B-GENE
2848 I-GENE
2849 I-GENE
2850 O
2851 O
2852 O
2853 O
2854 O
2855 O
2856 O
2857 O
2858 O
2859 O
2860 O
2861 B-GENE
2862 I-GENE
2863 I-GENE
2864 O
2865 B-GENE
2866 I-GENE
2867 I-GENE
2868 O
2869 O
2870 O
2871 O
2872 B-GENE
2873 I-GENE
2874 I-GENE
2875 O
2876 O
2877 O
2878 O
2879 O
2880 B-GENE
2881 I-GENE
2882 I-GENE
2883 O
2884 O
2885 O
2886 O
2887 O
2888 O
2889 O
2890 O
2891 O
2892 O
2893 O
2894 O
2895 O
2896 O
2897 O
2898 O
2899 O
2900 O
2901 O
2902 O
2903 O
2904 O
2905 O
2906 O
2907 O
2908 O
2909 O
2910 O
2911 O
2912 O
2913 O
2914 O
2915 O
2916 O
2917 B-GENE
2918 O
2919 O
2920 O
2921 O
2922 O
2923 B-GENE
2924 I-GENE
2925 O
2926 O
2927 O
2928 O
2929 O
2930 O
2931 O
2932 O
2933 O
2934 O
2935 O
2936 O
2937 O
2938 O
2939 O
2940 O
2941 O
2942 O
2943 O
2944 B-GENE
2945 I-GENE
2946 I-GENE
2947 I-GENE
2948 I-GENE
2949 O
2950 O
2951 O
2952 O
2953 O
2954 O
2955 O
2956 

4402 O
4403 O
4404 O
4405 O
4406 O
4407 O
4408 O
4409 O
4410 O
4411 O
4412 O
4413 O
4414 O
4415 O
4416 O
4417 O
4418 O
4419 O
4420 O
4421 O
4422 O
4423 O
4424 O
4425 O
4426 O
4427 O
4428 O
4429 O
4430 O
4431 O
4432 O
4433 O
4434 O
4435 O
4436 O
4437 O
4438 O
4439 O
4440 O
4441 O
4442 O
4443 O
4444 O
4445 O
4446 O
4447 O
4448 O
4449 O
4450 O
4451 O
4452 O
4453 O
4454 O
4455 O
4456 O
4457 O
4458 O
4459 O
4460 O
4461 O
4462 O
4463 O
4464 O
4465 O
4466 O
4467 O
4468 O
4469 O
4470 O
4471 O
4472 O
4473 O
4474 O
4475 O
4476 O
4477 O
4478 O
4479 O
4480 O
4481 O
4482 O
4483 O
4484 O
4485 O
4486 O
4487 O
4488 O
4489 O
4490 O
4491 O
4492 O
4493 O
4494 O
4495 O
4496 O
4497 O
4498 O
4499 O
4500 O
4501 O
4502 O
4503 O
4504 B-GENE
4505 I-GENE
4506 I-GENE
4507 I-GENE
4508 I-GENE
4509 I-GENE
4510 I-GENE
4511 I-GENE
4512 I-GENE
4513 O
4514 O
4515 O
4516 O
4517 O
4518 O
4519 O
4520 O
4521 B-GENE
4522 I-GENE
4523 O
4524 O
4525 O
4526 O
4527 O
4528 O
4529 O
4530 O
4531 O
4532 O
4533 O
4534 O
4535 O
4536 O


5571 O
5572 O
5573 O
5574 O
5575 O
5576 O
5577 O
5578 O
5579 O
5580 O
5581 O
5582 O
5583 O
5584 O
5585 O
5586 O
5587 O
5588 O
5589 O
5590 O
5591 O
5592 O
5593 O
5594 O
5595 O
5596 O
5597 O
5598 O
5599 O
5600 O
5601 B-GENE
5602 O
5603 O
5604 O
5605 O
5606 O
5607 O
5608 O
5609 O
5610 O
5611 O
5612 B-GENE
5613 O
5614 O
5615 O
5616 O
5617 O
5618 O
5619 O
5620 O
5621 O
5622 O
5623 B-GENE
5624 I-GENE
5625 O
5626 O
5627 O
5628 B-GENE
5629 O
5630 O
5631 O
5632 O
5633 O
5634 O
5635 O
5636 O
5637 O
5638 O
5639 O
5640 O
5641 O
5642 O
5643 O
5644 O
5645 O
5646 B-GENE
5647 I-GENE
5648 I-GENE
5649 I-GENE
5650 O
5651 B-GENE
5652 I-GENE
5653 I-GENE
5654 I-GENE
5655 O
5656 O
5657 O
5658 O
5659 O
5660 O
5661 O
5662 O
5663 O
5664 O
5665 O
5666 O
5667 O
5668 O
5669 O
5670 O
5671 O
5672 O
5673 O
5674 O
5675 O
5676 O
5677 O
5678 O
5679 O
5680 O
5681 O
5682 O
5683 O
5684 O
5685 O
5686 O
5687 O
5688 O
5689 O
5690 O
5691 O
5692 O
5693 O
5694 O
5695 O
5696 O
5697 O
5698 O
5699 O
5700 O
5701 O
5702 O
5703 O
5704

...

348321 O
348322 O
348323 O
348324 O
348325 O
348326 O
348327 O
348328 O
348329 O
348330 O
348331 O
348332 O
348333 O
348334 O
348335 O
348336 O
348337 O
348338 O
348339 O
348340 O
348341 O
348342 O
348343 O
348344 O
348345 O
348346 O
348347 O
348348 O
348349 O
348350 O
348351 O
348352 O
348353 O
348354 O
348355 O
348356 O
348357 O
348358 O
348359 B-GENE
348360 I-GENE
348361 O
348362 O
348363 O
348364 O
348365 O
348366 O
348367 O
348368 O
348369 O
348370 O
348371 O
348372 O
348373 O
348374 O
348375 O
348376 O
348377 O
348378 O
348379 O
348380 B-GENE
348381 O
348382 B-GENE
348383 O
348384 O
348385 O
348386 O
348387 O
348388 O
348389 O
348390 O
348391 O
348392 O
348393 O
348394 O
348395 O
348396 O
348397 O
348398 O
348399 O
348400 O
348401 O
348402 O
348403 O
348404 O
348405 O
348406 O
348407 O
348408 O
348409 O
348410 O
348411 O
348412 O
348413 O
348414 O
348415 O
348416 O
348417 O
348418 O
348419 O
348420 O
348421 O
348422 O
348423 O
348424 O
348425 B-GENE
348426 I-GENE
348427 O
348428 

349898 O
349899 O
349900 O
349901 O
349902 O
349903 O
349904 O
349905 O
349906 O
349907 O
349908 O
349909 B-GENE
349910 I-GENE
349911 O
349912 O
349913 O
349914 O
349915 O
349916 O
349917 O
349918 O
349919 O
349920 O
349921 O
349922 O
349923 O
349924 O
349925 O
349926 O
349927 O
349928 O
349929 O
349930 O
349931 O
349932 O
349933 O
349934 O
349935 O
349936 O
349937 O
349938 O
349939 O
349940 O
349941 O
349942 O
349943 O
349944 O
349945 O
349946 O
349947 O
349948 O
349949 O
349950 O
349951 O
349952 O
349953 O
349954 O
349955 O
349956 B-GENE
349957 O
349958 O
349959 O
349960 O
349961 O
349962 O
349963 O
349964 O
349965 O
349966 O
349967 O
349968 O
349969 O
349970 O
349971 O
349972 O
349973 B-GENE
349974 I-GENE
349975 I-GENE
349976 O
349977 O
349978 O
349979 O
349980 O
349981 B-GENE
349982 I-GENE
349983 I-GENE
349984 I-GENE
349985 I-GENE
349986 I-GENE
349987 I-GENE
349988 I-GENE
349989 I-GENE
349990 O
349991 O
349992 O
349993 O
349994 O
349995 O
349996 O
349997 O
349998 O
349999 O
350000 

351514 O
351515 O
351516 O
351517 O
351518 O
351519 O
351520 O
351521 O
351522 B-GENE
351523 O
351524 O
351525 O
351526 O
351527 O
351528 O
351529 O
351530 O
351531 O
351532 O
351533 B-GENE
351534 O
351535 B-GENE
351536 O
351537 B-GENE
351538 O
351539 B-GENE
351540 I-GENE
351541 O
351542 B-GENE
351543 O
351544 O
351545 B-GENE
351546 O
351547 O
351548 O
351549 O
351550 O
351551 O
351552 O
351553 O
351554 O
351555 O
351556 O
351557 O
351558 O
351559 O
351560 O
351561 O
351562 O
351563 O
351564 O
351565 O
351566 O
351567 O
351568 O
351569 O
351570 O
351571 O
351572 O
351573 O
351574 O
351575 O
351576 O
351577 O
351578 O
351579 O
351580 O
351581 O
351582 O
351583 O
351584 O
351585 O
351586 O
351587 O
351588 O
351589 O
351590 O
351591 O
351592 O
351593 O
351594 O
351595 O
351596 O
351597 O
351598 O
351599 O
351600 O
351601 O
351602 O
351603 O
351604 O
351605 O
351606 O
351607 O
351608 O
351609 O
351610 O
351611 O
351612 O
351613 O
351614 O
351615 O
351616 O
351617 O
351618 O
351619 O
351620

353352 O
353353 O
353354 O
353355 O
353356 O
353357 O
353358 O
353359 O
353360 O
353361 O
353362 O
353363 O
353364 O
353365 O
353366 O
353367 O
353368 O
353369 O
353370 O
353371 O
353372 O
353373 O
353374 O
353375 O
353376 O
353377 O
353378 O
353379 O
353380 O
353381 O
353382 O
353383 O
353384 O
353385 O
353386 O
353387 O
353388 O
353389 O
353390 O
353391 O
353392 O
353393 O
353394 O
353395 O
353396 O
353397 O
353398 O
353399 O
353400 O
353401 O
353402 O
353403 O
353404 O
353405 O
353406 O
353407 O
353408 O
353409 O
353410 O
353411 O
353412 O
353413 O
353414 O
353415 O
353416 O
353417 O
353418 O
353419 O
353420 O
353421 O
353422 O
353423 O
353424 O
353425 O
353426 O
353427 O
353428 O
353429 O
353430 O
353431 O
353432 O
353433 O
353434 O
353435 O
353436 B-GENE
353437 I-GENE
353438 O
353439 O
353440 O
353441 O
353442 O
353443 O
353444 O
353445 O
353446 O
353447 O
353448 O
353449 O
353450 O
353451 O
353452 B-GENE
353453 O
353454 O
353455 O
353456 O
353457 O
353458 O
353459 O
353460 O
3534

355160 O
355161 O
355162 O
355163 O
355164 O
355165 O
355166 O
355167 O
355168 O
355169 O
355170 O
355171 O
355172 O
355173 O
355174 O
355175 O
355176 O
355177 O
355178 O
355179 O
355180 O
355181 O
355182 O
355183 O
355184 O
355185 O
355186 O
355187 O
355188 O
355189 O
355190 O
355191 O
355192 O
355193 O
355194 O
355195 O
355196 O
355197 O
355198 O
355199 O
355200 O
355201 O
355202 O
355203 O
355204 O
355205 O
355206 O
355207 O
355208 O
355209 O
355210 O
355211 O
355212 O
355213 O
355214 O
355215 O
355216 O
355217 O
355218 O
355219 O
355220 O
355221 O
355222 O
355223 O
355224 O
355225 O
355226 O
355227 O
355228 O
355229 O
355230 O
355231 O
355232 O
355233 O
355234 O
355235 O
355236 O
355237 O
355238 O
355239 O
355240 O
355241 O
355242 O
355243 O
355244 O
355245 O
355246 O
355247 O
355248 O
355249 O
355250 O
355251 O
355252 O
355253 O
355254 O
355255 O
355256 O
355257 O
355258 O
355259 O
355260 O
355261 O
355262 O
355263 O
355264 O
355265 O
355266 O
355267 O
355268 O
355269 O
355270 O
3

In [77]:
pair_a = text_arr[0][:0]
pair_b = text_arr[0][0:10]
label = label_arr[0][:10]

pair_a = ["[CLS]"] + pair_a + ["[SEP]"]
label = ["[CLS]"] + label + ["[SEP]"]
label.insert(len(pair_a)-1, "[SEP]")

In [78]:
pair_a

['[CLS]', '[SEP]']

In [79]:
pair_b

['Immunohistochemical',
 'staining',
 'was',
 'positive',
 'for',
 'S',
 '-',
 '100',
 'in',
 'all']

In [80]:
label

['[CLS]',
 '[SEP]',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B-GENE',
 'I-GENE',
 'I-GENE',
 'O',
 'O',
 '[SEP]']

In [123]:
df = pd.read_pickle("../data/trials_topics_combined_all_years.pickle")
df["brief_t_and_s"] = df["brief_summary"] + " " + df["brief_summary"]
print(df.shape)
df.head()

(40203, 24)


score           id                                      brief_summary  \
0    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
1    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
2    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
3    1.0  NCT01774162  Endoscopic ultrasound (EUS) is a well-establis...   
4    1.0  NCT01226147  An open-label study to evaluate the efficacy a...   

                                         brief_title minimum_age  gender  \
0  EUS-guided Fine Needle Biopsy With a New Core ...        6570    male   
1  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
2  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
3  EUS-guided Fine Needle Biopsy With a New Core ...        6570  female   
4  Efficacy and Safety of Tamibarotene(AM80) for ...        7300  female   

                                     primary_outcome  \
0  Sampling Adequacy at time of procedure The abi...   
1  Sampling Adequacy at time of procedure The abi...   
2  Sampling Adequacy at time of procedure The abi...   
3  Sampling Adequacy at time of procedure The abi...   
4  Renal Function 24 weeks Urinary Protein values...   

                                detailed_description  \
0  Background: Endoscopic ultrasound (EUS) is a w...   
1  Background: Endoscopic ultrasound (EUS) is a w...   
2  Background: Endoscopic ultrasound (EUS) is a w...   
3  Background: Endoscopic ultrasound (EUS) is a w...   
4  Tamibarotene is a synthetic retinoid presently...   

                                            keywords  \
0  Endoscopic Ultrasound Fine needle aspiration F...   
1  Endoscopic Ultrasound Fine needle aspiration F...   
2  Endoscopic Ultrasound Fine needle aspiration F...   
3  Endoscopic Ultrasound Fine needle aspiration F...   
4          Lupus Nephritis SLE retinoid tamibarotene   

                                      official_title  ...  \
0  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
1  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
2  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
3  Endoscopic Ultrasound Guided Fine Needle Biops...  ...   
4                                                     ...   

                                           inclusion  \
0  - Adult patient 18 years or older - Able to re...   
1  - Adult patient 18 years or older - Able to re...   
2  - Adult patient 18 years or older - Able to re...   
3  - Adult patient 18 years or older - Able to re...   
4  - Steroid refractory lupus nephritis - more th...   

                                           exclusion topic  _ label  \
0  - No detectable lesion - lesion inaccessible t...    18  0     0   
1  - No detectable lesion - lesion inaccessible t...    27  0     0   
2  - No detectable lesion - lesion inaccessible t...    28  0     0   
3  - No detectable lesion - lesion inaccessible t...    30  0     0   
4  - Pregnant or breastfeeding female patients - ...     7  0     0   

                            disease                gene   age  year  \
0                 Pancreatic cancer  CDK6 Amplification  None  2017   
1         Pancreatic adenocarcinoma          KRAS, TP53  None  2017   
2  Pancreatic ductal adenocarcinoma               ERBB3  None  2017   
3         Pancreatic adenocarcinoma     RB1, TP53, KRAS  None  2017   
4                       Lung cancer        EGFR (L858R)  None  2017   

                                       brief_t_and_s  
0  Endoscopic ultrasound (EUS) is a well-establis...  
1  Endoscopic ultrasound (EUS) is a well-establis...  
2  Endoscopic ultrasound (EUS) is a well-establis...  
3  Endoscopic ultrasound (EUS) is a well-establis...  
4  An open-label study to evaluate the efficacy a...  

[5 rows x 24 columns]

In [3]:
import pandas as pd

df = pd.read_csv("../data/pm_labels_2017/clinical_trials_judgments_2017.csv")
df.head()

trec_topic_number  trec_doc_id pm_rel_desc disease_desc  \
0                  1  NCT00001188      Not PM          NaN   
1                  1  NCT00001189      Not PM          NaN   
2                  1  NCT00002185      Not PM          NaN   
3                  1  NCT00002466      Not PM          NaN   
4                  1  NCT00002641      Not PM          NaN   

  gene1_annotation_desc gene1_name gene2_annotation_desc gene2_name  \
0                   NaN        NaN                   NaN        NaN   
1                   NaN        NaN                   NaN        NaN   
2                   NaN        NaN                   NaN        NaN   
3                   NaN        NaN                   NaN        NaN   
4                   NaN        NaN                   NaN        NaN   

  gene3_annotation_desc gene3_name demographics_desc other_desc  
0                   NaN        NaN               NaN        NaN  
1                   NaN        NaN               NaN        NaN  
2                   NaN        NaN               NaN        NaN  
3                   NaN        NaN               NaN        NaN  
4                   NaN        NaN               NaN        NaN

In [9]:
df[~df["disease_desc"].isnull()]

trec_topic_number  trec_doc_id pm_rel_desc  disease_desc  \
54                     1  NCT00339404    Human PM   Not Disease   
55                     1  NCT00346008    Human PM   Not Disease   
61                     1  NCT00408018    Human PM   Not Disease   
68                     1  NCT00445783    Human PM  More General   
85                     1  NCT00577889    Human PM   Not Disease   
...                  ...          ...         ...           ...   
13422                 30  NCT02978547    Human PM         Exact   
13426                 30  NCT03000374    Human PM   Not Disease   
13431                 30  NCT03040986    Human PM         Exact   
13433                 30  NCT03058588    Human PM   Not Disease   
13434                 30  NCT03063203    Human PM   Not Disease   

      gene1_annotation_desc          gene1_name gene2_annotation_desc  \
54                    Exact  CDK4 Amplification                   NaN   
55                    Exact  CDK4 Amplification                   NaN   
61                    Exact  CDK4 Amplification                   NaN   
68                    Exact  CDK4 Amplification                   NaN   
85                    Exact  CDK4 Amplification                   NaN   
...                     ...                 ...                   ...   
13422          Missing Gene                KRAS          Missing Gene   
13426                 Exact                KRAS          Missing Gene   
13431                 Exact                KRAS          Missing Gene   
13433                 Exact                KRAS          Missing Gene   
13434          Missing Gene                KRAS          Missing Gene   

      gene2_name gene3_annotation_desc gene3_name demographics_desc  \
54           NaN                   NaN        NaN           Matches   
55           NaN                   NaN        NaN           Matches   
61           NaN                   NaN        NaN           Matches   
68           NaN                   NaN        NaN           Matches   
85           NaN                   NaN        NaN           Matches   
...          ...                   ...        ...               ...   
13422        RB1                 Exact       TP53           Matches   
13426        RB1          Missing Gene       TP53           Matches   
13431        RB1          Missing Gene       TP53           Matches   
13433        RB1          Missing Gene       TP53           Matches   
13434        RB1                 Exact       TP53           Matches   

          other_desc  
54     Not Discussed  
55     Not Discussed  
61     Not Discussed  
68     Not Discussed  
85     Not Discussed  
...              ...  
13422        Matches  
13426        Matches  
13431        Matches  
13433        Matches  
13434        Matches  

[3961 rows x 12 columns]

In [22]:
print(df[df["gene3_annotation_desc"] == "Exact"].shape)
df[df["gene3_annotation_desc"] == "Exact"]

(47, 12)


trec_topic_number  trec_doc_id pm_rel_desc   disease_desc  \
12955                 30  NCT00001827    Human PM    Not Disease   
12966                 30  NCT00019084    Human PM          Exact   
12979                 30  NCT00118365    Human PM    Not Disease   
12994                 30  NCT00367679    Human PM    Not Disease   
12999                 30  NCT00393029    Human PM   More General   
13001                 30  NCT00406445    Human PM    Not Disease   
13016                 30  NCT00544193    Human PM    Not Disease   
13060                 30  NCT00869258    Human PM          Exact   
13061                 30  NCT00894504    Human PM    Not Disease   
13070                 30  NCT00900328    Human PM    Not Disease   
13091                 30  NCT01029873    Human PM    Not Disease   
13093                 30  NCT01042535    Human PM    Not Disease   
13109                 30  NCT01103128    Human PM          Exact   
13124                 30  NCT01191684    Human PM          Exact   
13127                 30  NCT01198743    Human PM    Not Disease   
13149                 30  NCT01344837    Human PM    Not Disease   
13161                 30  NCT01387880    Human PM    Not Disease   
13162                 30  NCT01389414    Human PM   More General   
13172                 30  NCT01443468    Human PM    Not Disease   
13214                 30  NCT01737255    Human PM    Not Disease   
13248                 30  NCT01981525    Human PM    Not Disease   
13262                 30  NCT02062697    Human PM    Not Disease   
13268                 30  NCT02087176    Human PM    Not Disease   
13270                 30  NCT02101775    Human PM    Not Disease   
13281                 30  NCT02140723    Human PM    Not Disease   
13286                 30  NCT02171286    Human PM    Not Disease   
13300                 30  NCT02264613    Human PM    Not Disease   
13304                 30  NCT02285855    Human PM    Not Disease   
13305                 30  NCT02289326    Human PM          Exact   
13314                 30  NCT02340117    Human PM          Exact   
13323                 30  NCT02432963    Human PM          Exact   
13326                 30  NCT02448329    Human PM    Not Disease   
13327                 30  NCT02449655    Human PM    Not Disease   
13338                 30  NCT02518256    Human PM    Not Disease   
13341                 30  NCT02556281    Human PM          Exact   
13345                 30  NCT02576444    Human PM   More General   
13350                 30  NCT02595645    Human PM    Not Disease   
13356                 30  NCT02624973    Human PM    Not Disease   
13357                 30  NCT02642042    Human PM          Exact   
13363                 30  NCT02688907    Human PM    Not Disease   
13385                 30  NCT02790944    Human PM          Exact   
13386                 30  NCT02806648    Human PM  More Specific   
13396                 30  NCT02847000    Human PM          Exact   
13401                 30  NCT02893085    Human PM  More Specific   
13416                 30  NCT02965950    Human PM    Not Disease   
13422                 30  NCT02978547    Human PM          Exact   
13434                 30  NCT03063203    Human PM    Not Disease   

      gene1_annotation_desc gene1_name gene2_annotation_desc gene2_name  \
12955          Missing Gene       KRAS          Missing Gene        RB1   
12966          Missing Gene       KRAS          Missing Gene        RB1   
12979          Missing Gene       KRAS          Missing Gene        RB1   
12994                 Exact       KRAS          Missing Gene        RB1   
12999          Missing Gene       KRAS          Missing Gene        RB1   
13001          Missing Gene       KRAS          Missing Gene        RB1   
13016          Missing Gene       KRAS          Missing Gene        RB1   
13060     Different Variant       KRAS          Missing Gene        RB1   
13061                 Exact       KRAS     Different Variant       

In [29]:
df[(df["gene1_annotation_desc"] == "Exact")]

trec_topic_number  trec_doc_id pm_rel_desc  disease_desc  \
54                     1  NCT00339404    Human PM   Not Disease   
55                     1  NCT00346008    Human PM   Not Disease   
61                     1  NCT00408018    Human PM   Not Disease   
68                     1  NCT00445783    Human PM  More General   
85                     1  NCT00577889    Human PM   Not Disease   
...                  ...          ...         ...           ...   
13417                 30  NCT02974725    Human PM         Exact   
13420                 30  NCT02975752    Human PM   Not Disease   
13426                 30  NCT03000374    Human PM   Not Disease   
13431                 30  NCT03040986    Human PM         Exact   
13433                 30  NCT03058588    Human PM   Not Disease   

      gene1_annotation_desc          gene1_name gene2_annotation_desc  \
54                    Exact  CDK4 Amplification                   NaN   
55                    Exact  CDK4 Amplification                   NaN   
61                    Exact  CDK4 Amplification                   NaN   
68                    Exact  CDK4 Amplification                   NaN   
85                    Exact  CDK4 Amplification                   NaN   
...                     ...                 ...                   ...   
13417                 Exact                KRAS          Missing Gene   
13420                 Exact                KRAS          Missing Gene   
13426                 Exact                KRAS          Missing Gene   
13431                 Exact                KRAS          Missing Gene   
13433                 Exact                KRAS          Missing Gene   

      gene2_name gene3_annotation_desc gene3_name demographics_desc  \
54           NaN                   NaN        NaN           Matches   
55           NaN                   NaN        NaN           Matches   
61           NaN                   NaN        NaN           Matches   
68           NaN                   NaN        NaN           Matches   
85           NaN                   NaN        NaN           Matches   
...          ...                   ...        ...               ...   
13417        RB1          Missing Gene       TP53           Matches   
13420        RB1          Missing Gene       TP53           Matches   
13426        RB1          Missing Gene       TP53           Matches   
13431        RB1          Missing Gene       TP53           Matches   
13433        RB1          Missing Gene       TP53           Matches   

          other_desc  
54     Not Discussed  
55     Not Discussed  
61     Not Discussed  
68     Not Discussed  
85     Not Discussed  
...              ...  
13417        Matches  
13420        Matches  
13426        Matches  
13431        Matches  
13433        Matches  

[1486 rows x 12 columns]

In [64]:
df[(df["gene1_annotation_desc"].isnull()) & 
   (~df["gene2_annotation_desc"].isnull())]

Empty DataFrame
Columns: [trec_topic_number, trec_doc_id, pm_rel_desc, disease_desc, gene1_annotation_desc, gene1_name, gene2_annotation_desc, gene2_name, gene3_annotation_desc, gene3_name, demographics_desc, other_desc, gene_score]
Index: []

In [54]:
df[(df["gene1_annotation_desc"] == "Exact") & 
   (df["gene2_annotation_desc"].isnull()) & 
   (df["gene3_annotation_desc"].isnull())]

trec_topic_number  trec_doc_id pm_rel_desc  disease_desc  \
54                     1  NCT00339404    Human PM   Not Disease   
55                     1  NCT00346008    Human PM   Not Disease   
61                     1  NCT00408018    Human PM   Not Disease   
68                     1  NCT00445783    Human PM  More General   
85                     1  NCT00577889    Human PM   Not Disease   
...                  ...          ...         ...           ...   
12923                 29  NCT02906059    Human PM   Not Disease   
12928                 29  NCT02942706    Human PM   Not Disease   
12931                 29  NCT02964689    Human PM   Not Disease   
12935                 29  NCT02974725    Human PM   Not Disease   
12950                 29  NCT03089268    Human PM   Not Disease   

      gene1_annotation_desc          gene1_name gene2_annotation_desc  \
54                    Exact  CDK4 Amplification                   NaN   
55                    Exact  CDK4 Amplification                   NaN   
61                    Exact  CDK4 Amplification                   NaN   
68                    Exact  CDK4 Amplification                   NaN   
85                    Exact  CDK4 Amplification                   NaN   
...                     ...                 ...                   ...   
12923                 Exact                KRAS                   NaN   
12928                 Exact                KRAS                   NaN   
12931                 Exact                KRAS                   NaN   
12935                 Exact                KRAS                   NaN   
12950                 Exact                KRAS                   NaN   

      gene2_name gene3_annotation_desc gene3_name demographics_desc  \
54           NaN                   NaN        NaN           Matches   
55           NaN                   NaN        NaN           Matches   
61           NaN                   NaN        NaN           Matches   
68           NaN                   NaN        NaN           Matches   
85           NaN                   NaN        NaN           Matches   
...          ...                   ...        ...               ...   
12923        NaN                   NaN        NaN           Matches   
12928        NaN                   NaN        NaN           Matches   
12931        NaN                   NaN        NaN           Matches   
12935        NaN                   NaN        NaN           Matches   
12950        NaN                   NaN        NaN           Matches   

          other_desc  gene_score  
54     Not Discussed           2  
55     Not Discussed           2  
61     Not Discussed           2  
68     Not Discussed           2  
85     Not Discussed           2  
...              ...         ...  
12923  Not Discussed           2  
12928  Not Discussed           2  
12931  Not Discussed           2  
12935  Not Discussed           2  
12950  Not Discussed           2  

[1174 rows x 13 columns]

In [117]:
df_human_pm = df[~df["gene1_annotation_desc"].isnull()]
df_human_pm.head()

trec_topic_number  trec_doc_id pm_rel_desc  disease_desc  \
54                  1  NCT00339404    Human PM   Not Disease   
55                  1  NCT00346008    Human PM   Not Disease   
61                  1  NCT00408018    Human PM   Not Disease   
68                  1  NCT00445783    Human PM  More General   
85                  1  NCT00577889    Human PM   Not Disease   

   gene1_annotation_desc          gene1_name gene2_annotation_desc gene2_name  \
54                 Exact  CDK4 Amplification                   NaN        NaN   
55                 Exact  CDK4 Amplification                   NaN        NaN   
61                 Exact  CDK4 Amplification                   NaN        NaN   
68                 Exact  CDK4 Amplification                   NaN        NaN   
85                 Exact  CDK4 Amplification                   NaN        NaN   

   gene3_annotation_desc gene3_name demographics_desc     other_desc  \
54                   NaN        NaN           Matches  Not Discussed   
55                   NaN        NaN           Matches  Not Discussed   
61                   NaN        NaN           Matches  Not Discussed   
68                   NaN        NaN           Matches  Not Discussed   
85                   NaN        NaN           Matches  Not Discussed   

    gene_score  
54           2  
55           2  
61           2  
68           2  
85           2

In [59]:
df_human_pm["gene1_annotation_desc"][54]

'Exact'

In [101]:
def calc_gene_score(g1, g2, g3):
    print(g1, g2, g3)
    if g2 is np.NaN and g3 is np.NaN:
        print("1 gene")
        if g1 == "Exact":
            return 6
            elif g1 == "Missing Variant":
            return 2
        else:
            return 0
    elif g3 is np.NaN:
        print("2 genes")
        score_total = 0
        if g1 == "Exact":
            score_total += 3
        elif g1 == "Missing Variant":
            score_total += 1
        else:
            score_total += 0 
        
        if g2 == "Exact":
            score_total += 3
        elif g2 == "Missing Variant":
            score_total += 1
        else:
            score_total += 0
        
        return score_total
    else:
        print("3 genes")
        score_total = 0
        if g1 == "Exact":
            score_total += 2
        elif g1 == "Missing Variant":
            score_total += 1
        else:
            score_total += 0 

        if g2 == "Exact":
            score_total += 2
        elif g2 == "Missing Variant":
            score_total += 1
        else:
            score_total += 0

        if g3 == "Exact":
            score_total += 2
        elif g3 == "Different Variant":
            score_total += 1
        else:
            score_total += 0
        return score_total

In [76]:
g1_test = [
    "Exact", "Missing Gene", "Missing Variant", 
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant",
    "Exact", "Missing Gene", "Missing Variant"
]
g2_test = [
    np.NaN, np.NaN, np.NaN,
    "Exact", "Missing Gene", "Missing Variant",
    "Missing Gene", "Missing Variant", "Exact",
    "Missing Variant", "Exact", "Missing Gene",
    "Exact", "Missing Gene", "Missing Variant",
    "Missing Gene", "Missing Variant", "Exact",
    "Missing Variant", "Exact", "Missing Gene",
    "Exact", "Missing Gene", "Missing Variant",
    "Missing Gene", "Missing Variant", "Exact",
    "Missing Variant", "Exact", "Missing Gene",
    "Exact", "Missing Gene", "Missing Variant",
    "Missing Gene", "Missing Variant", "Exact",
    "Missing Variant", "Exact", "Missing Gene",
]
g3_test = [
    np.NaN, np.NaN, np.NaN, 
    np.NaN, np.NaN, np.NaN,
    np.NaN, np.NaN, np.NaN,
    np.NaN, np.NaN, np.NaN,
    "Exact", "Missing Gene", "Missing Variant",
    "Missing Gene", "Different Variant", "Exact",
    "Different Variant", "Exact", "Missing Gene",
    "Missing Gene", "Different Variant", "Exact",
    "Different Variant", "Exact", "Missing Gene",
    "Exact", "Missing Gene", "Different Variant",
    "Different Variant", "Exact", "Missing Gene",
    "Exact", "Missing Gene", "Different Variant",
    "Missing Gene", "Different Variant", "Exact",
]

for a, b, c in zip(g1_test, g2_test, g3_test):
    print(calc_gene_score(a, b, c))

Exact nan nan
1 gene
6
Missing Gene nan nan
1 gene
0
Missing Variant nan nan
1 gene
2
Exact Exact nan
2 genes
6
Missing Gene Missing Gene nan
2 genes
0
Missing Variant Missing Variant nan
2 genes
2
Exact Missing Gene nan
2 genes
3
Missing Gene Missing Variant nan
2 genes
1
Missing Variant Exact nan
2 genes
4
Exact Missing Variant nan
2 genes
4
Missing Gene Exact nan
2 genes
3
Missing Variant Missing Gene nan
2 genes
1
Exact Exact Exact
3 genes
6
Missing Gene Missing Gene Missing Gene
3 genes
0
Missing Variant Missing Variant Missing Variant
3 genes
2
Exact Missing Gene Missing Gene
3 genes
2
Missing Gene Missing Variant Different Variant
3 genes
2
Missing Variant Exact Exact
3 genes
5
Exact Missing Variant Different Variant
3 genes
4
Missing Gene Exact Exact
3 genes
4
Missing Variant Missing Gene Missing Gene
3 genes
1
Exact Exact Missing Gene
3 genes
4
Missing Gene Missing Gene Different Variant
3 genes
1
Missing Variant Missing Variant Exact
3 genes
4
Exact Missing Gene Different Var

In [118]:
import numpy as np

print(df_human_pm["gene2_annotation_desc"][85])
df_human_pm["gene2_annotation_desc"][85] is np.nan

nan


True

In [103]:
df_human_pm["gene_score"] = df_human_pm.apply(lambda row: calc_gene_score(
    row["gene1_annotation_desc"], row["gene2_annotation_desc"], row["gene3_annotation_desc"],
), axis=1)

Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan

Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing G

Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene

Missing Variant nan nan
1 gene
Different Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Different Variant nan nan
1 gene
Different Variant nan nan
1 gene
Different Variant nan nan
1 gene
Different Variant nan nan
1 gene
Different Variant nan nan
1 gene
Different Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Different Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Different Variant nan nan
1 gene
Exact nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Variant nan nan
1 gene
Different Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Gene 

Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene

Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Missing Variant nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Missing Variant nan nan
1 gene
Exact nan nan
1 gene
Missing Variant nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Variant nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Exact nan nan
1 gene
Missing Gene nan nan
1 gene
Different Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Different Variant nan nan
1 gene
Different Variant nan nan
1 gene
Different Variant nan nan
1 gene
Missing Gene nan nan
1 gene
Exact nan nan
1 gene
Missing Var

/Users/xu081/Documents/trec_t2/venv/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [112]:
df_human_pm.head()

trec_topic_number  trec_doc_id pm_rel_desc  disease_desc  \
54                  1  NCT00339404    Human PM   Not Disease   
55                  1  NCT00346008    Human PM   Not Disease   
61                  1  NCT00408018    Human PM   Not Disease   
68                  1  NCT00445783    Human PM  More General   
85                  1  NCT00577889    Human PM   Not Disease   

   gene1_annotation_desc          gene1_name gene2_annotation_desc gene2_name  \
54                 Exact  CDK4 Amplification                   NaN        NaN   
55                 Exact  CDK4 Amplification                   NaN        NaN   
61                 Exact  CDK4 Amplification                   NaN        NaN   
68                 Exact  CDK4 Amplification                   NaN        NaN   
85                 Exact  CDK4 Amplification                   NaN        NaN   

   gene3_annotation_desc gene3_name demographics_desc     other_desc  \
54                   NaN        NaN           Matches  Not Discussed   
55                   NaN        NaN           Matches  Not Discussed   
61                   NaN        NaN           Matches  Not Discussed   
68                   NaN        NaN           Matches  Not Discussed   
85                   NaN        NaN           Matches  Not Discussed   

    gene_score  
54           6  
55           6  
61           6  
68           6  
85           6

In [119]:
df_human_pm["disease_desc"].unique()

array(['Not Disease', 'More General', 'More Specific', 'Exact'],
      dtype=object)

In [120]:
disease_score_map = {
    "Exact": 3,
    "More General": 2,
    "More Specific": 2,
    "Not Disease": 0
}

In [121]:
df_human_pm["disease_score"] = df_human_pm["disease_desc"].map(disease_score_map)

/Users/xu081/Documents/trec_t2/venv/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [122]:
df_human_pm

trec_topic_number  trec_doc_id pm_rel_desc  disease_desc  \
54                     1  NCT00339404    Human PM   Not Disease   
55                     1  NCT00346008    Human PM   Not Disease   
61                     1  NCT00408018    Human PM   Not Disease   
68                     1  NCT00445783    Human PM  More General   
85                     1  NCT00577889    Human PM   Not Disease   
...                  ...          ...         ...           ...   
13422                 30  NCT02978547    Human PM         Exact   
13426                 30  NCT03000374    Human PM   Not Disease   
13431                 30  NCT03040986    Human PM         Exact   
13433                 30  NCT03058588    Human PM   Not Disease   
13434                 30  NCT03063203    Human PM   Not Disease   

      gene1_annotation_desc          gene1_name gene2_annotation_desc  \
54                    Exact  CDK4 Amplification                   NaN   
55                    Exact  CDK4 Amplification                   NaN   
61                    Exact  CDK4 Amplification                   NaN   
68                    Exact  CDK4 Amplification                   NaN   
85                    Exact  CDK4 Amplification                   NaN   
...                     ...                 ...                   ...   
13422          Missing Gene                KRAS          Missing Gene   
13426                 Exact                KRAS          Missing Gene   
13431                 Exact                KRAS          Missing Gene   
13433                 Exact                KRAS          Missing Gene   
13434          Missing Gene                KRAS          Missing Gene   

      gene2_name gene3_annotation_desc gene3_name demographics_desc  \
54           NaN                   NaN        NaN           Matches   
55           NaN                   NaN        NaN           Matches   
61           NaN                   NaN        NaN           Matches   
68           NaN                   NaN        NaN           Matches   
85           NaN                   NaN        NaN           Matches   
...          ...                   ...        ...               ...   
13422        RB1                 Exact       TP53           Matches   
13426        RB1          Missing Gene       TP53           Matches   
13431        RB1          Missing Gene       TP53           Matches   
13433        RB1          Missing Gene       TP53           Matches   
13434        RB1                 Exact       TP53           Matches   

          other_desc  gene_score  disease_score  
54     Not Discussed           2              0  
55     Not Discussed           2              0  
61     Not Discussed           2              0  
68     Not Discussed           2              2  
85     Not Discussed           2              0  
...              ...         ...            ...  
13422        Matches           2              3  
13426        Matches           2              0  
13431        Matches           2              3  
13433        Matches           2              0  
13434        Matches           2              0  

[3961 rows x 14 columns]

In [104]:
df_gene["gene_score"].unique()

array([6, 0, 3, 1, 2, 4])

In [105]:
df["disease_desc"].unique()

array([nan, 'Not Disease', 'More General', 'More Specific', 'Exact'],
      dtype=object)

In [106]:
df["gene1_annotation_desc"].unique()

array([nan, 'Exact', 'Missing Gene', 'Missing Variant',
       'Different Variant'], dtype=object)

In [107]:
df["gene2_annotation_desc"].unique()

array([nan, 'Missing Gene', 'Exact', 'Missing Variant',
       'Different Variant'], dtype=object)

In [108]:
df["gene3_annotation_desc"].unique()

array([nan, 'Exact', 'Missing Gene', 'Different Variant'], dtype=object)